In [8]:
!pip install transformers
!pip install sentencepiece

  Using cached sentencepiece-0.1.97-cp39-cp39-win_amd64.whl (1.1 MB)


In [30]:
!pip install editdistance
!pip install ai4bharat-transliteration==0.5.0.3

  Using cached pydload-1.0.9-py2.py3-none-any.whl (16 kB)
  Using cached Flask_Cors-3.0.10-py2.py3-none-any.whl (14 kB)
  Using cached progressbar2-4.2.0-py2.py3-none-any.whl (27 kB)
  Using cached python_utils-3.5.2-py2.py3-none-any.whl (24 kB)


In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader
from tqdm import tqdm
import os
from sklearn.metrics import classification_report, f1_score
from torch.utils.data import Dataset
import collections
import emoji
import re
from emot.emo_unicode import EMOTICONS_EMO
from bs4 import BeautifulSoup
import nltk
nltk.download('words')
import nltk, string, re, spacy,unicodedata, random
nltk.download('punkt')
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.tokenize import ToktokTokenizer
from langdetect import detect
from ai4bharat.transliteration import XlitEngine

C:\Users\cs\anaconda3\envs\cuda_FYP1\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[nltk_data] Downloading package words to
[nltk_data]     C:\Users\cs\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\cs\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
device = 'cuda'
device = device if torch.cuda.is_available() else 'cpu'

In [13]:
#loading the training dataset
train = pd.read_csv('Dataset/tamil_offensive_full_train.csv', delimiter="\t", error_bad_lines=False, header=None, names=['text', 'label', 'nan'])
train = train.drop(columns=['nan'])
train.dropna()
train['label'] = pd.Categorical(train.label)
train

C:\Users\Admin\AppData\Local\Temp/ipykernel_5436/3578742339.py:2: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train = pd.read_csv('Dataset/tamil_offensive_full_train.csv', delimiter="\t", error_bad_lines=False, header=None, names=['text', 'label', 'nan'])


text          label
0                      movie vara level la Erika poguthu  Not_offensive
1      I love Ajith Kumar Vivegam movie inki mjy bht ...      not-Tamil
2              Padam nalla comedy padama irukum polaye..  Not_offensive
3      karthick subburaj anne .... intha padam vetri ...  Not_offensive
4      கவுண்டர் தேவர்.சார்பாக வெற்றி பெற வாழ்த்துக்கள் 🦁  Not_offensive
...                                                  ...            ...
35134  Trending number #2 idhukku nammalam karanamnu ...  Not_offensive
35135  Movie script super, athuvum HIP HOP Tamizha mu...  Not_offensive
35136                       Just 3k likes for 300k likes  Not_offensive
35137                          Aaloo le lo. Kanda le lo.      not-Tamil
35138  நாமக்கல் மாவட்டம்  வன்னியர் சார்பாக திரௌபதி பட...  Not_offensive

[35139 rows x 2 columns]

In [99]:
val = pd.read_csv('Dataset/tamil_offensive_full_dev.csv', delimiter="\t", error_bad_lines=False, header=None, names=['text', 'label', 'nan'])
val = val.drop(columns=['nan'])
val.dropna()
val['label'] = pd.Categorical(val.label)
val.dtypes

C:\Users\Admin\AppData\Local\Temp/ipykernel_5436/1318495689.py:1: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  val = pd.read_csv('Dataset/tamil_offensive_full_dev.csv', delimiter="\t", error_bad_lines=False, header=None, names=['text', 'label', 'nan'])


text       object
label    category
dtype: object

In [3]:
def deEmojify(string):
    emoji_pattern = re.compile("["
                              u"\U0001F600-\U0001F64F"  # emoticons
                              u"\U0001F300-\U0001F5FF"  # symbols & pictographs
                              u"\U0001F680-\U0001F6FF"  # transport & map symbols
                              u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
                              u"\U00002500-\U00002BEF"  # chinese char
                              u"\U00002702-\U000027B0"
                              u"\U00002702-\U000027B0"
                              u"\U000024C2-\U0001F251"
                              u"\U0001f926-\U0001f937"
                              u"\U00010000-\U0010ffff"
                              u"\u2640-\u2642"
                              u"\u2600-\u2B55"
                              u"\u200d"
                              u"\u23cf"
                              u"\u23e9"
                              u"\u231a"
                              u"\ufe0f"  # dingbats
                              u"\u3030"
                              "]+", flags=re.UNICODE)
    return emoji_pattern.sub(r'', string)
        
def preprocess(text):
    text = str(text)
    text = deEmojify(text) #convert emojis to their defns in words, they might be useful
    text = re.sub(r'([\.\'\"\/\-\_\--])',' ', text) # remove punctuations , removes @USER / some abbreviatins
    to_remove_url = ('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|'
      '[!*,]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')
    text = re.sub(to_remove_url,'',text)  # remove url patterns
    text = re.sub(" \d+", " ", text)
    text = text.replace(","," ")
    text = re.sub(r'(?:^| )\w(?:$| )', ' ', text).strip()
    punctuation='!!"$%&()*+-/:;<=>?[\]^_{|}~.'
    text = ''.join(ch for ch in text if ch not in set(punctuation))
    # text = text.translate(str.maketrans('', '', string.punctuation))
    text = BeautifulSoup(text, 'html.parser').get_text()
    # Stopword Removing
    tokenizer = ToktokTokenizer()
    # convert sentence into token of words
    tokens = tokenizer.tokenize(text)
    tokens = [token.strip() for token in tokens]
    text = ' '.join(ch for ch in tokens)
    return text 

def clean(df):
    df['text'] = df['text'].apply(lambda x: preprocess(x))

#clean(train)
#clean(val)

In [66]:
e = XlitEngine("ta")
def transliterate(text):
    try: 
        lang = detect(text)
        if lang == 'ta':
            return text
        elif lang != 'en':
            out = e.translit_sentence(text, beam_width=10)
            print(out['ta'])
            return out['ta']
        return text
    except:
        return text
    
train['text'] = train['text'].apply(lambda x: transliterate(x))

Loading ta...
மோவி வேற லேவில் லா எரிகா பொகுது
லோவ் அஜித் குமார் விவேகம் மோவி இங்கி மேஜி பட் அச்சி லி
படம் நல்ல காமெடி படாம இருகும் போலை
கார்த்திக் சுப்பராஜ் அன்னி இந்த படம் வெற்றி அடைய உணகளுக்கு என்னுடய வழ்துக்கள்
இப்போ இந்த டிரைலர் ஆக் பற்குறவன ஒரு லிக் பொடுங்க
நெற்கொண்டா பர்வை சேமா சேமா சேமா டிரைலர்
கோரிக் எங்க அப்பா மில்லிட்டரி டா ஓடி விளையாட சொல்லி தருவாயா
டிஸ்லிக் போட்டவன் ராதம் காக்கி தா சவான்
ஆனந்தி ஆர்மி ஹிட் லிக் எண்ணெயும் இபி ஆக்கிட்டிங்களே அனந்தி #அன்புக்குநாணடிமை
தலைவா மாஸ் நடிப்பின் நாயகன் சூர்யா அன்ன பான்ஸ் ஹிட்ஸ் லிக்
லோவ் விஜய் அன்ன ரூர் சோ கேட் அன்ன
டே ராஜினி பவம் டா நை வரவேன் போராவின் எல்லம் கரிதுப்பத கொறைய பேசிட்டு இருக்கன் 58
தனுஷ் பான்ஸ் ஹிட் லிக் ஹெர்
டே டே டெய் லூசு பசங்கள முன்னா பின்ன ஜெயலலிதா அம்மா வா பத்துகின்களாட கம்பீரம்னா என்னனு அவங்க கண்ணுள்ள தா பாகனும் அம்மா ஓடா ஹிஸ்டரி ஆக் இது சோனியா காந்தி மேரி இருகு சே அவங்க பீயோ எடுகனுமான சீ பத்துட்டு வந்து எடுங்கடா டம்மி அக்காதிங்க
ஆதி என்ன பா டிப்பரெண்ட் ஆவ் இருகு சாமா
விஸ்வசம் தேசர் கூ ஆப்ராம் எற்றம் இங்க வந்தீங்க


உங்களுக்கு வயசே அகல சிட்டி லோவ் மா
நோ காப்பான் தேசர் மார்ச்சிங் டோவர்ட்ஸ் வீவ்ஸ் லிக்ஸ்
ரோம்பா நலைக்கு அப்ரோ நா எதிர்பார்தமாறிரி படம்
ஆமா மர் பாண்டி இங்க எண்ணா பன்றாரு
கோமாளி காததன் அக பொகுது படம் ஒத்திக்கும்
விஜய் செதுப்பதி மட்டும் வில்லன் நா இருந்த வேசிக்கோ படம் பிளாப் தான்
வேரா வேரா வா வேரா வா பைரவ
ஓஹ் ஆ தெலுகு ரேமா ஆப் ரவி டிஜாஸ் பெண்கள் டிகர்
தலைவா பக்க மாசஸ் ஒன்லி ஒன் சூப்பர் ஸ்டார்
நோ மேன்ஸ் நோ எந்த டிலாகோ தலாய தவற ஏறு சோன்னா நல்லை தராயலா
நான் அரசியலுக்கு வருவது உறுதி சேமா
லா லா லா சூர்விவ தல வால்க் ஐஸ் ஜஸ்ட் எனுக்
லெஸ்ட் பிம் உண் அழைகில் எண் இதயம் தான் நிலையில் கதி சாங் ஆக் கோபி அடிச்சன்
சேரிஸ் கே தரப் சே கிசி கோ ஹெர்ட் மிள ஹேய்
டெக் லா யரால் இந்த வீடியோ பக்கிக அவக மதும் லிக் போடுக
பிங் படம் பாதுதேன் தி பிரிண்ட் இறுகு ஏற வேணும்
வேரி பேட் நா எத்தர் பார்த்த அளவுக்கு இல்ல
பரியேறும் பெருமால் படம் வரும் பொது மட்டும் சொன்னிக்க இதுவும் சமூக படம் தா திஸ் பெர்சின்டாஜ் டிரு சப்போர்ட்
1மே வீவ்ஸ் லிக்ஸ் #ஸ் #ஹீரோ
வேர் லேவில் லெஸ்ட் சென் பூவிளி
படம் வேற லேவில் திருமா கூ வோ ரஞ்சித் நை கூ வோ 

புல்ஜஞ்ஸ் சீர் ஜீ ஹிந்தி மே பீ சாஹியே
நீங்க வேணா அரியா லா க்ளாஸ் ஆக் போஸ் ஆக் சுதலம் ஆண எண் மாஸ் என்னனு தெரியது லா
குச் சம்மா நி பிர் அச்சா லா டிரைலர்
ரிப் வான் விங்கிள் ஸ்லீபிங் பீட்டி
லிக் பேட்டா தலைவர் பக்க தான போரிங்க இந்த பேட்டா ஓடா ஆட்டத ஆல்
தலைவர் தா தலைவர் தா வேற லேவில்
இந்த மதிரி ரோல் சிவகர்த்திகேயன் கூ செட் அகது விலாக் சப்பிக் ஒன்லி சர்ஸ் போர் ஹிம் வேற அக்டர் பானி இருந்த மாஸ் ஆய் இருகும்
காலிக் லா லைப் சிறிச்சதி இப்பாலம் சிறிக்க கோடா உணர வேலா வேலா நூ அலைய வேண்டியது
சோ பெர் டிஸ்லிக் பப்பா பசங்க பவுண்ட்
சூர்யா நா சும்மாவா சூர்யா எப்பவும் மாஸ் டா
யாறு இந்த டிஸ்லிக்ஸ் அந்த கைலா கேடாச சேதனிங்க
எண்ட மோகன்லால் ஒரு ஆளுனு அவனுகு ஒரு முக்கியமான ரோல் குடித்திரிங்கேலே கேதா பேசுரதுக்கு வேற ஆலி கிடைகிலய இதுல அர்ய யும் இருகன் எண்ணா கொடுமா சீர் இது படம் நிச்சையம் சேமா ஹிட் ஆகும்
கொள்ள கெண்ட் லா இருகே நோ காம்பீட்டியன் ஒன் மே
அடினா டா எல்லரும் கிராமா கப்படற்று வியவசயத்தா காப்ரண்னென்னு
அன்னன் கிடுக்கி டிரைலர் மரானா மாஸ் அன்னா உம்மா வைட்டிங் போர் டிசம்பர்
கங்கன ஆஸ் ஜே லலிதா யா ஜீடலால்
எதிர் பக்க

வோ அரி யூ தல டா தல போல வரும
மலையாளி இல்லாத பாட் உண்டோ மலையாளி மசன்மர் ஆதி லிக்
கருணாஸ் சப்போர்ட் டோ ஹீரோ லூக்ஸ் லிக் தேவர் சப்போர்ட் டோ வண்ணியர்
ஆப்டர் சிரா செங் சீர் அன்ற
ஹெய் வந்து சென்றனை ஸ்டர் பிம் சான்சே ஐஸ் இல்ல ராம்மானிய
லிக் ஆதி இன் ஹாரில் ஆகனம்
எண்ணா டா போமா படம் மாதிரி இறுகுது
எண்ணா தான் காலம் மரணலும் அந்த சதி வேரி அடங்க மற்றங்கு மோதல கோவர்மண்டா சதி வேரி புடிச்பட இருகு ஸ் வேலா பிக் வெல்ல இல்ல எண்ணா டா ஏடு இந்தியா
கோல கண்டு லே இருக்கென் கொள்ளமா விடமாட்டன் சேமா
தலைவாயாகானா சோப்பர் லோவ் யூ தலைவாயாகானா பேட்டா பராக்
வோ ஐஸ் கெட்டிங் கோசபும்ஸ் லிக் #வடசென்னை #அசுரன் #கொலமசு
சூப்பர் டிரைலர் பட் லெஸ்ட் சென் திசப்பாய்ந்தேட்
படம் நல்லா இருக்கும்ம் நல்லா இருக்கானும்
ரசிச்சி எடுதுருக்கன்ய பழய ராஜினி ஸ்டீல் டியாலகுஸ் வெறித்தனமான் படம் சேமா மாஸ் ஆக் இருகும்
ஓவ் மை கோட்ட்ட்ட்ட்ட்ட் வாட் வாட் வொண்டர்புல்
பான்ஸ் மரானா வைட்டிங் நண்ப ரீயா
காமண்ட் செக்சன் புல் ஆக் ஒரி சாதி புண்டய இருக்கு
தா தலைவர் வேற லேவில் பன்னிறுகரு அசுரா வீ8ஐங் தலைவா சீக்கிரம் வா எழுந்து வா
மரானா மாஸ் அம் வாக் போர் மரானா வைட்

வேற லேவில் இப்பா பேசுங்கடா மோக்க நூ தலைவான
691கீ ரேச்செட் ஆன நம்பா மிசன் இன்னும் முடில்ல லிக்ஸ் வரணும்
அம் வைட்டிங் லெஸ்ட் பிட்டு வெறிதானாமம்
சிங்கம் சிங்கம் ரோஸ் ஒல்வேற்ஸ்ஸ்
மரானா வைட்டிங் ஒன்லி தல
ஆபி தல எல்ல கேட்டுப் லேம் ஸ்மார்ட் இருகிங்க
தளபதி தாண்டா முடிமா நெறுப்புளம் எங்க கிட்ட பருப்புடா
எண்ணா டா தும்ஞென் ஆக் சூர்யா அன்ன பைரவ விஜய் போல இருக்குறாரு
ரிலீஸ் இன் தெலுகு கார்த்தி அன்ன
விஸ் அன்ன ஸ்டர் அன்ன பான்ஸ் மட்டும் லிக் பணுங்கா
படம் எண் ஜாதி கூ சப்போர்ட் பென்ற மாதிரி இருக்கு ஜாதி இல்லாமா இருந்ததானே ஒற்றுமை ஓடனே எல்ல பேரும் அவர் அவர் ஜதி கரங்க சார்ப படம் வெற்றி பேற வழ்துக்கள் நூ சொல்ரிங்க இதுல இருந்தே தெரியுது ஒங்க ஒற்றுமை எண்ணா ஜாதிய இருந்த எண்ணா எல்ல பேரும் காமண்ட் பன்றது இந்த காமண்ட் பாக்ஸ் லா தானே மனுசன் கண்டு பிடிச்ச யூட்டுப் கே தெரியுது பட் மனுசனுக்கு தெரியலையே ஜாதி இனம் லா நம்மா கண்டு பிடிப்பது தானே ஒரு காலதுள்ள எதோ ஒருதன் கண்டு பிடிச்ச அதுக்கு ஒங்களுக்கு எண்ணா சமந்தம் இந்த காமண்ட் பாக்ஸ் லா யே நம்மா ஒற்றுமை சேதரிருச்சு
எது டிரைலர் ஆக் இல செரியல் ஆக்
யாவ் கவ் பிரகாஷ் நே மிய

...

யவ் ஒரு மனுஷன் எத்தன கேட்டுப் லா யா நடிக்கிறது
008 டப் எங்கினீரிங் பூலிகோ ஹிட் லிக்
சேமா காஸ்ட் ஆல் வில்லான்ஸ் இன் ஒன் கொம்போ சூப்பர்
நாடாக காதல் கும்பலை அடியோடு அளிக்க வேண்டும்
ஒன் பீர் தையைவர் சிறபான தரமண சம்பவங்காக இனிமே தான் பகபோரிங்க
மியூச் கேட்டா மதிரி இருக்கு இது எண்ணா மியூச்
உண்டிக் மேன்ஸ் ஸ்டோமச் பர்ன்ஸ் ஓவர் லோட்ஸ் சாவுங்க டா ஹேட்டர்ஸ்
எட் சேம்ஸ் லிக் விஸ்வசம் தேமே மியூச் நூ பாதலி சிறிப்பு தா வருது
இதங்கு பதில வேற யராவது ஹீரோ வா நடிசிற்களம் போய்யும் பொய் நீயா தூ
இன்னும் கொஞ்சம் பீட்டர் ஆக் பன்னிறகளம் அணிவாய் தளபதிக்காக பாடலம்
சூப்பர் மிண்ட் போளவிங் டிரைலர் ஜெய் சூப்பர் ஸ்டார் ராஜானிகாண்டா சீர்
அப்போ ர்ஸ் பாலாஜியா கோபி பண்ணுரிங்கள சூரிய
வெற்றி பேற வேதும் விஜய் அன்ன வெறியன்
ரவணன் எதுலையும் ரவனான கேட்டவன கட்டுறதுக்கே படம் எடுபிங்கள டா
டிரைலர் பக்கா பட் அல்டிமேட்டு மாஸ் ஐஸ் யூ1 பிம்
இது யார யமத்ரிங்க மரானா பங்கம்
ஆல் மேக் உப் ஐஸ் லூகிங் லிக் பேக் நாட் ரேல்
அம் தே டன் வணகம் சல்லாம் தியாகு
டிரெண்டிங் நோ இன் சிறிலங்கா தல போர்ட் திலாயா
அர்ய அண்ட் சேசா இங்கையுமா
அனைத்து தேரா மக்களும் 

யாவ் பாண்டி நே இணய இங்க அங்க பொய் குடா கேள்வி தான யா கேட்குற
தர்மபூரி மக்கல் சர்பாக படம் வெற்றிபெற வாழ்துகள்
செம்மே மோக்க டே ஹவா ஹவா ஹவா குபேர் நூ சிரிச்சவன் எல்லம் கே தூகு
யூ1 மூசி வேற லேவில் வா தலைவ நை
ஒன்னும் புரியல ஆண எடிட்டிங் சேமா மாஸ் தேசர்
122 டே என்னட தேடிய பய்யா டிரெக்ஸ் ராணா எங்க தளபதி நடிப்பு பாத உணக் சிறிப்பு வருத கொம்மளமரியாட்யா கேட் பென்ற இந்த சென் ஆய் இல்லி ரிலீஸ் அவமே பண்ணிடுவே நை அஜித் ஐஸ் கிண்டல் பண்ணு இல்லினா ஏற வேணாலும் கிண்டல் பண்ணு தளபதி ஐஸ் கிண்டல் பாண அரோடா ஒத்தா பூண்ட
சேமா சூப்பர் மோவி மாஸ் வேற லேவில்
கைய்ஸ் மேக் எட் ஆஸ் மில்லியன் சூன்
046 டீக் டோக் வாலோ கே லை
காபான் வேபு கிடைச்ச திருப்பி பொட்டு ஒப்பான்
உண்டிக் பண்ணவ அவா அம்மா எல்லம் ஈட்டம் தா தேவா பசங்கள உங்கம்ம கூதிங்கள கிளிச் பீ சூர்யா அன்ன பிக் ரசிகை
தரமண சம்பவம் காத்துட்டு இருக்கு திவாளி கூ பிகில் விஸ் கைதி
சிவா அன்ன சேமா பதில் ஆதி காங்கிரடுலீஷன்ஸ்
பிம் வாஸ் சூப்பர் சூர்யா ராக்கிங் ஆஸ் ந்
அட்னி பேடி ஸ்டார் காஸ்ட் பீர் யார் ஹிந்தி மேன் பீ ரிலீஸ் கரோ
பாலிவுட் கா பாப் ஹேய் கிலாடி குமார்
யார் எண்ணா சொன்னலும் 

பிங் # அமிதாப் பச்சன் பட் அஜித் சீர் ஐஸ் கிர்8
மரானா மாஸ் தேசர் சாங் டிரைலர் இலமே சேமா படமும் செமாயா இருகும்
எற்றம் விட்ல அதிவி பண்ணும்போதும் திட்டும்போதும் சிறிபா ஸ்டி பணமுடியமா பல கடிசிருகின்க
அன்னி ஜெயம் மோவி லூவர் பவோரிட் மோவி
ஒரு திருத்தம் பிரிட்டிஷ் காரன் கிடா சுதந்திரம் வாங்கினது மக்கல் இல்ல அரசியல் வாதிகள் புரிஞ்சவன் பிஸ்தா
ரிபாத் மோடு லா டிரைலர் பக்கிரவன் மட்டும் லிக் பொடுங்க
கிகி சேரி நி பெண்ணோ டோ லோக் வோட் நி டெங்கை
யே டோ பிங் கா ரேமா ஹேய்
கார்த்திக் சுப்பராஜ் எல்ல ராஜினி பட்டதாயும் எடுது பார்து தலைவர ஒரு வழி பண்ணி இருகர்ணு நெனைகிறேன் சிறபான தரமண சம்பவம் சூப்பர் லிக்
என்னங்கட ரோபோ கூ தோப்பை தள்ளிருக்குஷாம கேவளம் டா டே
அம் இப்பவே எண்ணல இருக உணர தல ரூர் உஞ்சம்பராப்டில் ஹிஸ்டரி ஐஸ் காயிங் டோ சாங்கை
தல மாஸ் யுவான் அல்டிமேட்டு
மரானா மாஸ் தேசர் கோல மாஸ் டிரைலர்
டிரைலர் பாகமே லிக்ஸ் போர் ஸ்டர்
பத் சேமா மாஸ்
இல் பாட் கு அட் வாய்ட் சா
யரெல்லாம் தல மோவி கூ வேட் பன்றிங்க
எட்டன் அண்ட் அன்னன்
போர் அஜித் அக்டிங்கா போர் விஜய் ஓவர் அக்டிங்கவாகாக ஹஹஹ ஹஹஹா ஹஹஹ ஹஹா ஹஹஹஹஹா ஹஹஹஹஹா ஹஹஹஹஹஹாகாஹாக ஹ

ஜெரோ மோவி கீ டோ வாட் லாகின் வாலி ஹேய்
எண்ட போனோ இப்பல் படம் கண்டு இறங்கியதே உள்ளு சூப்பர் பிலிம் அடிபொளி
என தான் தளபதி பான் ஆக் இருந்தலும் இந்த டிரைலர் கூ எல்லருக்கும் பிடிசு இருக்கும் டிரைலர் ஆக் இந்த போடு அப்போ படம் பாத்
வடகுரன் சார்க்கர் நமகு அடுக்கலாம் நாரன் சரியான சாய்ஸ்
மரானா மாஸ் மரானா ஸ்டீல் மார்ன் கேது மாஸ் டிரைலர் ராஜினிபிய்ட்
பேட்டா செமாயா பொய்நுது போய்ங்களுக்கு சுவேத் தா
சேமா டிரைலர் பாகா மாஸ்
அம் பிக் தல பான் தல கிடா இருபுற ஹார்வர்க் டெடிக்கேஷன் எல்ல சீயான் விக்ரம் சீர் கிட்ட சோ அவர ரோம்பா பிடிக்கும்
ஏர்ல எந்திரன் டிரைலர் ரா பத்துட்டு வந்திங்களோ அவங்கலாம் லிக் பொடுங்க
எண்ணா இரெந்தலும் தல நா உசுர் டா
அஜித் சீர் காங்கிராட்ஸ் வருசத்துகு ஒரு படம் வந்தலும் அதும் வேற லேவல் லா இருகு சீர் லோவ் தல
மஞ்சு செச்சி குரவும் கோடி உள்பெட்டுத்தனம் அயிருணோ
ஒரிஜினல் வெர்சன் எண்ணவோ கன்னட தான் ஆண தமிழ் டிரைலர் தான் வீவ் லிக்ஸ் அதிகம்
சம்மா சம்மா என்ன பாஸ்ட் ஆய் பொகுது பா
தாறு மாறு பட் சிங்கம் தேமே இருந்த மாஸ் ஷா இருண்டிருக்கும்
படம் ரிலீஸ் தேத் பொடுங்க பா வெரித்தனமா வைட்டிங்
டெஸ் டோ கோ ந்
மார்ன

இது என்னட எங்க அம்மா கூ வந்த சோதன
699 லிக்ஸ் ரேச்செட் ஏற்றுக்
13 மில்லியன் வீவ்ஸ் எப்பா வரும் இனும் டெஸ் ஆகுமா
விஜய் சேதுபதி போவர் வீவ்ஸ் பட் லிக்
வேற லேவல் தனுத் வெற்றி மரன் கிப் கொம்போ
யோகி பாபு அன்ன அவரு ஹெர் ஸ்டீல் லா கேது சாவா ஹரி காட் பன்னிட்டு நல்லாவில்
பக்க சூப்பர் ஹிட் அந்திரா சூர்யா பான்ஸ்
விஜய் சேதுபதி கா இந்த படாத பருங்க பா
இந்த படதுல கேது மாஸ் காற்ற தலாய நடிகள் இந்த படதுல இந்த நாடோட இன்றைய உண்மைய சொல்ற அஜித் குமார் ஆக் நடிசிற்காறு #ஸ்டோபுமோனபுஸ்
ஹமே லில் பட் டா ஈஸ்
எனக்கு தெரிஞ்சு ரெண்டு படமும் பிளாக்பஸ்டர் தான்
மஹா நடிகன் விஜ் சேதுபதி
கேக்கா பேக்கா சோர்ட் பிலிம் பதவங்கா லிக் பண்ணுங்க
மு பே மது மக்கி காட் கே கே ஐஸ் லாக் ராகா ஹேய்
ஆல் மை பவ் ஸ்டார்ட் ஸ்டர் தலிவா
டிஸ்லிக் போட்டா எல்லரும் தல தளபதி பான்ஸ் ஆக் இருப்பங்களோ
யார் யார் லாம் இந்த மோவி ஓடா பிளோசாட்டை ரிவி கூ வேட் பன்றிங்க லிக் பொடுங்க பக்ளம்
பான் ஆப் சூப்பர் ஸ்டார் @ தெலங்கானா
போஸ்மேன் ஒரு ஜீ5 சேரிஸ் இருக்கு அதுலா அந்த மனுசன் வருசம் கோமா போய்டுவன் பிறகு வந்து பார்த்தா எல்ல மற்றிழிருக்கும்
படம் வேற லேவில் காமெடி ஆக் இ

In [69]:
train.to_csv('tamil_train_translit.csv')

In [67]:
val['text'] = val['text'].apply(lambda x: transliterate(x))

ஹாண்டோம் ஹுங் கேரி வா தலைவா
ஜெய் வாஸ் ஐம் பிரவோ போர் கிளிப் டே மார்டி கு éகோட் ஆ டொயிலட்
வேற லேவில் பிம் சேமா டிரைலர்
#காப்பான் ஐஸ் கோன்னா பெய் மாசிவ் ஹிட் #சூரிய #சூரிய38
250கீ லிக்ஸ் டோ கோ ஏரளம் வைட்டிங்
சூபர் அன்னன் டிரைலர் செம்மையா இருகு அம் வைட்டிங் அஞ்ஞங்மானா
மரணம் வே லூவ் சூர்யா அண்
அப்பாலுட்டா ஹார்வர்க் லாட் ஆப் லூவ் இளம்புயல் ஜெயம் ரவி
சன்னி லியோன் பான்ஸ் ஹிட் லிக்
தாகா பான்ஸ் ஆக் இரு தா லிக் போடுக
தெரிக்க வேலாடமா கி
ராஜினி அரசியல் வேற லேவில்
டே எண்ட உங்களுக்கு இந்தே இல்லாத வெல்ல சூர்யா லிக் ஜோக்கர் டா
ஏங்க சீயான் விகாரம் எப்போ மாவா மாஸ் டா
தல இன்னும் இபி புல் வீட் இவ்வளவு நாள் நடிப்பெண்க கடுப்ப இருக்கு தல
போஸ்மேன் வெப் சேரிஸ் இந்த படம் மாதிரி தான் இருகும்
500கீ நீட் டோ வீவ்ஸ்
வோ சேமா டிரைலர் படம் வெற்றி அடைய தளபதி பான்ஸ் சார்பக விஷஸ் டோ சூர்யா சீர்
ராஜினி ஸ்க்ரீன் லா சேமா ஜோர் ஆக் இருகரு சூப்பர்
டே பொங்க டா தமிழ் நாற்ற ரேப் கிரிமி இன்பிரிஸ் அகித்தி பொகுது எவனசு கெகுரேகா லா எபோ வந்து வாழ்துகள் மன்னகட்டி நூ உண்மைய பொன்ன மதிகுறத இருந்த எனோட சிண்ட் கூ அம்மா தங்கட்சி வசு ரிப்ளி பன

டிரைலர் லா இவளோ நர்ரீஷன் அல்மோஸ்ட் ஸ்டோரி ரேவில் பண்ணி படத்துக்கு குபுதுற மாறி மானி சீர் ஆல மட்டும் தான் முடியும்
எத்தன பேர் தா அணை மரானா வைட்டிங்
ரேமா ஆப் ஹிந்தி மோவி பிங் கோட் ஒன்
சூர்யா சீர் சிங்கம் லோக் லிக் ஒரிஜினல் லியான்
தலைவ வேற லேவில் வெறித்தனம் எண்களுக்கு இதனால் கத்து கேடாச போக்கிஷம் யுவிமூசிக் பிசுடாய நே
ஐய்யோ தல யூ வில் சே மை ராஜ்
761 லிக்ஸ் ரேச்செட் ஏற்றுக்
அப்டியெல்லாம் நாடு நாடாகவும் கூடாது இந்த சென் கூ தியேட்ரில்
கிப் பிம் லா பின்னிட யாவா
#1 டிரெண்டிங் நோ இன் அந்திரா அண்ட் தெலங்கானா
நை தேசர் கீப் எட் உப் பட் அஞ்சான் மோவி மதிரி பனிராதின்க
யூ1 செல்வராகவன் வேற லேவில் கொம்போ
ஜெயம் ரவி பான் பிரோம் அந்திரா பிரதேஷ்
ஒம்மாள ஒரு புண்டையும் புரியல எண்ணா சன்னி இது
செம செம சப்போர்ட் சப்போர்ட் பன்றவங்க ஹிட் லிக்
சூப்பர் தியேட்டர் லா பக்க மாஸ் ஆக் இருக்கும்
க்ளாஸ் மாஸ் தல யுவான்
வேற லேவில் டா எப்பா மரானா வைட்டிங்
தலான் லோவ் யூ ஸ் சிவகர்த்திகேயன் அன்ன பான்ஸ்
யாம் விஜய் பான் பட் சூர்யா அன்ன அல்வேஸ் மாஸ்
கம்மலா அம்மா வா எண்ட கெவள படுதுரிங்க மூடி லோக் சாங்கை உப் பண்ணுங்க டா
லூக்ஸ் லிக் கோ

ஷே லூக்ஸ் லிக் டம்மி மாம் கீ கூடிய
டிரம் டிரட் மக்கல் செல்வான் பான்ஸ் லிக் எட்
தலைவா விஜய் நா செம்மா ஆல் சென்னிஸ் சூபெரப்பப்ப்
இந்த கேலாட்டு நாய இந்தமாரி பது ரோம்பா நாளசு நலார்குட டிரைலர்
வாட்சிங் அகைன் அண்ட் அகைன் #சூர்யா அன்ன மாஸ் பண்ணிடிங்க
மை பவோரிட் சாங்
எபோ தான் எங்க தல சார்க்கர் கூ ஏத மாறி டிட்லிஸ் வட்சிருக்கறு லிக் மிஸ்கின்
தலை விடுதலி பாரடா லிக் தாட் டோன்
ஹப்பி நேவ் ஏற் எல்லரும் பொண்களுக்கு மீட் பானலம்
39கீ லெப் போர் லிக்ஸ்
ஹவா ஹவா ஹவா ஹவா ஹவா அம் வைட்டிங்
டோபோல் ஆச்சன் மக்கல் செல்வான் வேற
டிரைலர் ஏஸ் இவ்லோ மொக்கய இருகு படம் எந்த லெட்சநாதுள்ள இருகோ
மாஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ்ஸ் நா அது தல தனானானா மசீ
டே கடைசி வரைகும் வித்ய பலன் நா காட்டவே இல்லயே ஈஸ் அஜித் சீர் கூ ஜோடி வித்ய பலன் பட் அவங்கள டிரைலர் லா காமிக்கவே இல்லயே
அனில்ஸ் குஞ்சுகள் டூஷன் லேவ் போட்டு டிஸ்லிக் பண்டன் போல
தளபதி வில்லன் கூ ஒரு லிக் போடு
ஜெயரை ரவி பான்ஸ் ஹிட் லிக்
சூப்பர்ஸ்தர இப்படி வசு செய்வேங்கனானு நான் எதிர்ப்பாகவே இல்ல வேற லேவில் டிரைலர்
எப்போ படம் வரும் செய்கிறாம் சொல்லு டா
வோ ஐஸ் பெஸ்ட்

அர்ஜுன் மலையாளம் மோவி மரக்கர் கட்டா வைட்டிங்
இந்த டிரைலர் ஆய் டிஸ்லிக் பண்டியா சிறிக்க தெரியாத வான் போல
145 ஐஸ் லிக் பிகில் கிராண்ட்
ரஜினிகாந்த் பான்ஸ் ஹிட் லிக் லோவ் பிரோம் மகாராஷ்ட்ரா
சேமா மாஸ் நா ஆர் பிம் வேற லேவில்
சோ பெர் சூரி நாய்ஸ் டிரைலர் பதுருகு அண்ட் அவனுகளுக்கு நிக் ஆக் இருந்திருக்கும் தல நா சும்மாவா
கோமா லா இருந்த வயசு ஆகத போரோ
அல்வேஸ் மாஸ் டிரைலர் கண்டிபா இந்த மோவி காலிவுட் கே பெருமை சேர்கும்
போற போக்க பாத ஓர் நாளு லா லிக்ஸ் வரபோகுது
உயிரே ஏ குடுப்பென் தல காகா லோவ் தல சோ மூச்
ஹிந்தி ரேமா கா ஏறுதலும் தமிழ் லா பாகும் பொது நல இருகு
பேட்டா விஸ் விஸ்வசம் லிக் பேட்டா காமண்ட்ஸ் விஸ்வசம்
வேற லேவில் கா நிகா வேற லேவில்
அர்ய சசேஷ காபன் சூட்டிங் லா தான் மரா பானி முடிவு பானி எருபங்களோ
ஸ்டர் பான் பிரோம் சிங்கப்பூர் ஹெர் வைட்டிங் போர் தே கிங் டோ கோம் ஒன் ஸ்க்ரீன் டா
இனாடா தல தால்பதி நூ இலரியும் எழுகிறான்
சூரிய அன்ன நேகா வேற லேவில்
இந்த பொலப்புக்கு பிச்சை எடுக்கலாம் டா மாவு தலா
டே இனாடா ஒரு அந்நோன்சிமெண்ட் இலாத விதிங்க
776கீ அதே நீகழ எண்களுக்கு கம்பீட்டர் அதா யினி வச கோடா இட்டது போல தளபதி

2019 கே கொரிலா பிளாப் சீரு வேட் அண்ட் சே
என தல வேற லேவில் லா பானி இறுகெங்க லூவ் சோ முச்சல
காமிங் சூன் ஆக் அப்பா ஆகஸ்ட் ரீல்ஸ் இல்லியா
கோஸ் அகர் பஞ்சாபி கானே பீ ஐசை ஹோட்
யாரெல்லாம் விசேதுபதி ஓடா என்றிய திரும்பி திரும்பி பாதிங்களோ லிக் பொடுங்க
500கீ லிக்ஸ் ஹிட் லிக் எப் யூ அரி காயிங் போர் பிட்ஸ்
அக்ஷர விவேக் அஜித் 3
எண்ணா எல்லம் அவான் செயல் கோபி யா
வேற லேவில் சீ கொம்போ
சூப்பர் ஹோ சூப்பர் டெர்லிங் சூர்யா உம்மக
தாங்க் யூ வினோத் சேமா சேமா மோக்க
இவ்லோ ஜேதி பேர் சொல்றிக அப்பதி என மேறு இருகு உங்க ஜதீலா அண்ட் எண் எதிலையும் தான் பட் இந்த மோவி கூ சப்போர்ட் பன்றது தேபு இல பட் இவ்லோ ஜேதி நாமே எங்க இருந்து வார்து அட்லிஸ்ட் ஒன் மோவி தான் இது மக்கல் முட்டல் தான் இனும்
அமித்தா பேக்கன் மோவி ரேமா
டிஸ்லிக் பென்னா எல்லரும் டாவிட் பசங்க தானு சொல்றவங்க மட்டும் இங்க லிக் பண்ணுங்க
முருக்கு மேச லா சூரிய அன்ன வேற லேவில்
பாய் மேன் கிட்னா சேர்ச் கியா திஸ் சாங் டப் ஜேக் நிலா ஹேய்
மோபைல் கைலா எடுக்கும் போதெல்லா இங்க வரவன் ரிப்ளி பண்ணு
சூர்யா சூப்பர் மோகன்ளல் டப்பிங் வேரி பேட்
கேக்கா பேக்கா சோர்ட் பிலிம் லாங்கி வெர்ச

...

தா யாறு யா நே கார்த்திக் சுப்பராஜ் பா மரணம்
மரானா மாசஸ் தல நா சும்மாவா
என்னட லிக்ஸ் வீவ்ஸ் இன்னும் சரி ஆகலையா லிக் தான் இருக்கு
தும்ஞென் லா விஸ் வைகாம விட்டுடிங்க சோ வீவ்ஸ் கம்மி ஆக் தான் வரும்
யூ1 பிம் ஹேட்ஸ் லா கேகுபோது புல் அறிகுதுய
விஜய் சேதுபதி பான்ஸ் ஹிட் லிக்
விஸ்வசம் லா சாங் அடிசித்துக்கு சாங் இந்து லா சேம் டூன் சொல்லி பாறு கா சாங் பாராக விடு பாராக விடு அடிசி பாராக விடு
மாஸ் மாஸ் மாசஸ் விஸ் அன்ன மாஸ் வேற லேவில் பாண்ட் வேற லேவில்
நுவ்வு சூப்பர் அன்ன சூரிய பாய் லோவ் யூ
புள்ளிங்கோ கேதி அய்ய சாமி பிகிலோடா பிள்ஸ் கைதிய விடதெங்க
சமா சூப்பர் தல மேசன்ஸ் ஒரு லிக் பொடுங்க
சென்சே அமி ஜாக்சன் ஆஸ் வில்லன்
எந்த கேது மாஸ் எறுகுட வரும் தலைவர் கூ மட்டும் அது சோது மாஸ் காட்டுறதுல கெத்து டாட் பாய்ஸ் சே
தல வோ சேமா மாஸ் குகா மாஸ் தல
சிக்ஸ் பேக் சீசிகு வேட் பணுரன் கிங் மேகர் வா கா செக்கிறும்
பங்காளிகளா இத வேகம் பாத்தது இன்னும் வேகாமா லிக் ஆக் தெரிக்க விடுங்க இண்ணைகுள்ள மில்லியன் லிக்ஸ் வரணும்
காமல் ஹஸ் பிப் போட்டம் மக்கல் நீதி மையம்
வேளாளர் சரபா படம் வெற்றி அடைய வழ்துக்கள்
நமா வேடு பிள்ளை ஸ் மோவி ஐஸ

தளபதி பான் பட் விஜயேசுபதி ரோம்பா புடிக்கும்
பாஷா பார்த்த பீல் இருக்கு தாங்ஸ் போர் பிரிங்கிங் ராஜினி பேக் கார்த்திக் சுப்பராஜ்
ஆரம்பம் சூப்பர் காப்பி சொலு தலை கூ சிறிப்பு வரள
போ டா டே இது இல்லம் ஒரு படம்
800கீ லிக்ஸ் கீ காமண்ட்ஸ்
இது தாண்டா டிரைலர் கோக்கா மக்க
சரி தான் டா டே அப்பூடியோ படம் நல்ல இருத்த சரி
விக்ரம் கேட்டுப் அண்ட் சால்ட் அண்ட் பப்பர் லோக் வேற லேவில்
செல்வராகவன் சீர் தே கிங் ஐஸ் பேக் எணி நாராய பிளிம் எடுக சீர் நான் உங்க பான்
அம் கிட் யுவான் பான்
மரணம் வைட்டிங் விஜ்64 நோ பிகில்
வாட் டிரைலர் தலையாசாசாசாசாசாசாயா லூகிங் மோர் ஹாண்டோம் அண்ட் அசோம் குடோஸ் டோ தே கிரிய்ட்டர்ஸ்
எண்ட தமிழ் நட்டு காரணுக மட்டும் இப்படி வேரி பீடித்து அலிராணுகா
எண்ட ராஜினி எபோ டா லா வரணு சோனரு பொய் பேசி ஹுமர் பானி படம் ஒட்டுற அளவுகு ஜெயம் ரவி மார்க்கெட் மோசாமா இருகுனு அர்தம்
படம் வேற லேவில் லா இறுகும் போலயே
எண்ணெக்கு இண்ட தேவா இல்லாத சாங் டென்சி லாகிக் இல்லாத பிக்ட் ஆக் லாம் விதா போரிங்கா
வெல் டோன் சூப்பர் மாஸ் கொலமாசஸ் மோவி
மாட்ட இவான் இந்த சினீமையிலு மக்களே காப்பதுற தேமே தான
செக் பிம் லிக் #விஸ்வசம்
ஹோப

எண் கடவளை தலைவரி வைட்டிங் போர் உர் தரிசனம் பிரோம் கர்னாடாக
தளபதி பான் அண்ட் சே பக்க மாஸ்
அன்னன் வேர் லேவில் லூ சூர்யா அன்ன பிரோம் நடிப்பின் நாயகன் பான்ஸ் இன் கேரள
டே இது டம்ப் அண்ட் டம்பர் தானே
ஜஸ்ட் லூக்ஸ் லிக் கார்ட்டூன் சோ பேட்
இதுக்கு தீபா வா நடிக்க வேகு இருக்கலம்
ஏரளம் கோமெல் டிரைலர் ரிபாத் மோடு பகுரெங்கா ஹிட் லிக் ஹெர்
தல வேற லேவில் லூவ் தல
விஸ்வசம் மோடன் பிக்டர் பத்துட்டு எங்க வந்து டிரைலர் பது வேரி எதிகுறவங்க லிக் போட்டும் பொங்க
சேதுபதி அன்ன சேமா மாசா இருகிங்க
கோயியேல் சேமா மாஸ் பிம் டா ஓவ் மை யுவான்
சேமா சேமா பயங்கரம் சூப்பர்ப் வேற லேவில்
கண்டிபா படம் பிளாப் ரிசன் சூரி அண்ட் தே கிரட் வில்லன் பகர அப்போ வே சேமா பயமா இருகு
செமாயா இருகு பா லோவ் வூ
பிம் பிரோம் டோ வேர் லேவில்
சொல்லுங்க எண் பொண்டாட்டி தான் ஐயோ இலய அவங்க எண் லூவர்
தேரி ரிலீஸ் ஆகி இண்ணைக்கு ஏற் ஆகுது
தல வேற லேவில் ஸ்கி வாவா தல
ஜாதி ஜாதி நூ சொல்லிட்டு சாகரப்பா என கொண்டு போகா போரிங்கா எல்லாரும் ஓவோருதனுக்கு பின்னாடியும் ஒவோரு ஜாதி கோடம் லாம் இருக்கும் அத நல்லவன் யாரும் வெளிகாட்டிகமாட்டான் படத்த படமா பாருங்க பா அது நம்மா 

இந்த பொண்கள் சேமா சூப்பர் ஆக் இருக பொது
ஹிப் ஹாப் ஆதி அன்ன பான்ஸ் லிக்
இந்த மனுஷாமிஷ்கின் எண்ணைகுத எல்ல லிக் ஆக் யும் ஒன் பண்ணி படம் எடுக போராரோ
இந்த பிம் மோபைல் லா பியானோ மியூச் ஆப் உச் பென்னா அதுலா வரும்
பொள்ளசுலா பொணுங்கள பென்னா அசிங்க பூதே ஜேதிகரான எங்க பா கணோம்
தலைவ சூப்பர் வழ சங்கர் சீர் டீம்
028 கிட்ஸ் ரெபரென்ஸ் மாடில இருந்து குடிச்ச சக்திமான் காபத்
அன்பு அன்னம் சூப்பர் போரோ கோரிக் குஸ்டியன்ஸ்
என சீர் ராஜினி கூ ரஜ்னி நூ வருது
அம் விஜய் பான் பட் லிக் தல சோ மூச் சாமா மசா இருக்கு
200கீ லிக்ஸ் நீடேட் போர் லிக்ஸ்
அரி யூ விற்கின் தல
மரானா மோரானா மரானா வைட்டிங் மரானா மாஸ்
ஒரு படம் பத பெல் வேற லேவில் மியூச்
கிளிமாக்ஸ் மியூச் கேக்கும்போது ஆப்டியே கோசபும்ஸ் ஸ்டார்ட் ஆகுது தாங்ஸ் யுவான் அன்னங்
தோல்வி உந்தன் பட்டது உச்சம் எரி கொடிக்கு
ரேல் லைப் படாம எடுதிருக்குறரு மகன் அவர்கள்
1ஸ்ட் டீம் டென்காக் மோவி தமிழ் கேட் சினீமா டிடாக் மெங்கீச்பேகன் பெஸ்ட் ஓ பிண்டங்
டே டிஸ்லிக் பொடுரங்க கோய்ன் பத்துட்டு பொடுங்க டா
சட்டா கிளிகரா சென் சூமா தியேட்டர் ஏ கிளியும் தல மாஸ்
அந்யன் வெற்றி மரன் சீர் பான் லிக் 

வந்துதெனு சொல்லு திரிம்பி வந்தேனு தேறு முன்னடி இபிடி பொன்னேனு அபிடியே திரிம்பி வந்தேனு சொல்லு பேட்டா டா மரானா மாஸ் டா
தலைவ உன்ன அடிச்சுக்க இனிமேலும் பொறந்து ஏறும் வேற போறது இல்ல
ராஜினி அரசியலுக்கு தேற நம்புறவங்க ஒரு லிக் பொடுங்க
குஞ்சமாவது புரூர மதி பொடுங்கட பக்க உணர
சேமா டிரைலர் சூப்பர் சூர்யா பான்ஸ் லிக்
நமக்கு தவியானதா நாமா தான் அடிசி வங்கனும்
டாப் வெற்றி சீர் பிரவோ பிரவோ பிரவோ
வந்த ராஜாவா மட்டும் தா எண் தலைவன் ஸ்டர்
விஜய் சேதுபதி அரன் விஜய் பிரகாஷ் ராஜ் சிம்பு செனபாட்டி இன்றோ தியாகு இன்றோ எதி இன்றோ
நமக்கு எதுகு இந்த தவ இல்லாத வல மர் ராம்
இது கேகா பேகா கேகா பேகா சோர்ட் பிலிம் ஓடா கோபி
மாயாவரம் மாணிகோண்டு எங்க ஊரு இல்ல நம்மா ஊரு போற்ற லிக்
ஸ்டீல் ஆப்டர் டெஸ் காப்பான் தேசர் ஐஸ் டிரெண்டிங் இன் சிறிலங்கா
வேடுநலும் குதுநலும் அடிசி சொலுவான் நா தல ரசிகன் டா
சேமா மாஸ் துரை சிங்கம் வேதா வேதா வடா
பாதுகிட்டே இருகனும் போல இருகு டவ் நே வா தலா
கங்கன கோ சபாலாட்டா கா நாசா சேட் காயா ஹேய் இஸ்கா வேசா ஹீ ஹால் ஹோகா ஜோ ஹால் விவேக் ஒபராய் கா மோடி கே மோவி மே ஹூவா தா ஆப் கோ லேக் கே மேன் ஐஸ் ரோல் மேன் நாஹி ச

In [70]:
val.to_csv('tamil_dev_translit.csv')

In [65]:
from ai4bharat.transliteration import XlitEngine
e = XlitEngine("ta")
out = e.translit_sentence("vanakkam ulagam !", beam_width=10)
print(out)

Loading ta...
{'ta': 'வணக்கம் உலகம் !'}


0                        movie vara level la Erika poguthu
1        love Ajith Kumar Vivegam movie inki mjy bht ac...
2                  Padam nalla comedy padama irukum polaye
3        karthick subburaj anne intha padam vetri adaya...
4          கவுண்டர் தேவர் சார்பாக வெற்றி பெற வாழ்த்துக்கள்
                               ...                        
35134    Trending number #2 idhukku nammalam karanamnu ...
35135    Movie script super athuvum HIP HOP Tamizha mus...
35136                                 Just likes for likes
35137                              Aaloo le lo Kanda le lo
35138    நாமக்கல் மாவட்டம் வன்னியர் சார்பாக திரௌபதி படம...
Name: text, Length: 35139, dtype: object

In [4]:
train = pd.read_csv('tamil_train.csv')
val = pd.read_csv('tamil_dev.csv')
train.drop(['Unnamed: 0'], axis=1, inplace=True)
val.drop(['Unnamed: 0'], axis=1, inplace=True)
train.dropna()
train['label'] = pd.Categorical(train.label)
val.dropna()
val['label'] = pd.Categorical(val.label)
train['text'].apply(str)
clean(train)
clean(val)
train

text          label
0                        மோவி வேற லேவில் லா எரிகா பொகுது  Not_offensive
1      லோவ் அஜித் குமார் விவேகம் மோவி இங்கி மேஜி பட் ...      not-Tamil
2                     படம் நல்ல காமெடி படாம இருகும் போலை  Not_offensive
3      கார்த்திக் சுப்பராஜ் அன்னி இந்த படம் வெற்றி அட...  Not_offensive
4        கவுண்டர் தேவர் சார்பாக வெற்றி பெற வாழ்த்துக்கள்  Not_offensive
...                                                  ...            ...
35134  டிரெண்டிங் நம்பர் #2 இதுக்கு நம்மலாம் காரணம்னு...  Not_offensive
35135  மோவி ஸ்கிரிப்ட் சூப்பர் அதுவும் ஹிப் ஹாப் தமிழ...  Not_offensive
35136                           ஜஸ்ட் லிக்ஸ் போர் லிக்ஸ்  Not_offensive
35137                              ஆலோ லே லோ கண்டா லே லோ      not-Tamil
35138  நாமக்கல் மாவட்டம் வன்னியர் சார்பாக திரௌபதி படம...  Not_offensive

[35139 rows x 2 columns]

In [5]:
class tamil_Offensive_Dataset(Dataset):
    def __init__(self, encodings, labels, bpe = False):
        self.encodings = encodings
        self.labels = labels
        self.is_bpe_tokenized = bpe

    def __getitem__(self, idx):
        if not self.is_bpe_tokenized:
            item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        else:
            item = {
                'input_ids': torch.LongTensor(self.encodings[idx].ids),
                'attention_mask': torch.LongTensor(self.encodings[idx].attention_mask)
            }
        item['labels'] = torch.tensor(self.labels[idx])
        return item

    def __len__(self):
        return len(self.labels)

In [6]:
from transformers import XLMRobertaTokenizer, XLMRobertaForSequenceClassification
tokenizer = XLMRobertaTokenizer.from_pretrained('xlm-roberta-base')
model = XLMRobertaForSequenceClassification.from_pretrained('xlm-roberta-base', num_labels=3)
model_name = 'XLMroberta_base_tamil_weighted'

Some weights of the model checkpoint at xlm-roberta-base were not used when initializing XLMRobertaForSequenceClassification: ['lm_head.dense.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.bias', 'roberta.pooler.dense.weight', 'lm_head.bias']
- This IS expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLMRobertaForSequenceClassification were not initialized from the model checkpoint at xlm-roberta-base and are newly initialized: ['classifier.dense

In [7]:
 # Optimiser
from transformers import AdamW
optimizer = AdamW(model.parameters(), lr=1e-5)

C:\Users\cs\anaconda3\envs\cuda_FYP1\lib\site-packages\transformers\optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


In [8]:
label_mapping = {
        'Not_offensive': 0, 
        'not-Tamil': 1, 
        'Offensive': 2, 
    }

In [9]:
# Collecting Text and Labels
train_batch_sentences = list(train['text'])
train_batch_labels =  [label_mapping[x] for x in train['label']]
dev_batch_sentences = list(val['text'])
dev_batch_labels =  [label_mapping[x] for x in val['label']]

In [10]:
# Convert to Tensor
if 'parameters' in tokenizer.__dict__.keys() and tokenizer.__dict__['_parameters']['model'] == 'ByteLevelBPE':
    train_encodings = tokenizer.encode_batch(train_batch_sentences)
    dev_encodings = tokenizer.encode_batch(dev_batch_sentences)
else:
    train_encodings = tokenizer(train_batch_sentences, padding='max_length', truncation=True, max_length=64, return_tensors="pt")
    dev_encodings = tokenizer(dev_batch_sentences, padding='max_length', truncation=True, max_length=64, return_tensors="pt")

train_labels = torch.tensor(train_batch_labels)
dev_labels = torch.tensor(dev_batch_labels)

In [11]:
# Defining Datasets
train_dataset = tamil_Offensive_Dataset(train_encodings, train_labels, bpe = False)
dev_dataset = tamil_Offensive_Dataset(dev_encodings, dev_labels, bpe = False)

device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
model.to(device)
best_val_f1 = 0
count = 0

In [13]:
# Alternate Loss Fn
# Weighted Manual Loss Function
from sklearn.utils import class_weight
import torch.nn as nn
weights = class_weight.compute_class_weight(class_weight = 'balanced',classes = np.unique(train_batch_labels),y = train_batch_labels)
weights = np.exp(weights)/np.sum(np.exp(weights))
class_weights = torch.FloatTensor(weights).to(device)
loss_function = nn.CrossEntropyLoss(weight=class_weights, reduction='mean')

In [14]:
# Dataloaders
train_loader = DataLoader(train_dataset, batch_size=16, shuffle=True)
dev_loader = DataLoader(dev_dataset, batch_size=16, shuffle=False)
loss_weighted = True

In [16]:
for epoch in range(30):
    train_preds = []
    train_labels = []
    total_train_loss = 0
    model.train()
    print("==========================================================")
    print("Epoch {}".format(epoch))
    print("Train")
    for batch in tqdm(train_loader):
        optimizer.zero_grad()
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['labels'].to(device)
        outputs = model(input_ids, attention_mask=attention_mask, labels=labels)
        if loss_weighted:
            loss = loss_function(outputs[1], labels)
        else:
            loss = outputs[0]
        loss.backward()
        optimizer.step()

        for logits in outputs[1].detach().cpu().numpy():
            train_preds.append(np.argmax(logits))
        for logits in labels.cpu().numpy():
            train_labels.append(logits)
        total_train_loss += loss.item()/len(train_loader)

    print("Dev")
    dev_preds = []
    model.eval()
    total_val_loss = 0
    with torch.set_grad_enabled(False):
        for batch in tqdm(dev_loader):
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['labels'].to(device)
            outputs = model(input_ids, attention_mask=attention_mask, labels=labels)
            if loss_weighted:
                loss = loss_function(outputs[1], labels)
            else:
                loss = outputs[0]
            total_val_loss += loss.item()/len(dev_loader)

            for logits in outputs[1].cpu().numpy():
                dev_preds.append(np.argmax(logits))

    y_true = dev_batch_labels
    y_pred = dev_preds
    target_names = label_mapping.keys()
    train_report = classification_report(train_labels, train_preds, target_names=target_names)
    report = classification_report(y_true, y_pred, target_names=target_names)
    val_f1 = f1_score(y_true, y_pred, average='macro')

    if val_f1 > best_val_f1:
        PATH = 'finetuned_models/' + model_name + '.pth'
        torch.save(model.state_dict(), PATH)
        model.save_pretrained(os.path.join('finetuned_berts/', model_name))
        best_val_f1 = val_f1
        count = 0
    else:
        count += 1

    print(train_report)
    print(report)
    print("Epoch {}, Train Loss = {}, Val Loss = {}, Val F1 = {}, Best Val f1 = {}, stagnant = {}".format(epoch, total_train_loss, total_val_loss, val_f1, best_val_f1, count))
    if count == 5:
        print("No increase for 5 epochs, Stopping ...")
        break

Epoch 0
Train


  0%|          | 0/2197 [00:00<?, ?it/s]C:\Users\cs\anaconda3\envs\cuda_FYP1\lib\site-packages\ipykernel_launcher.py:9: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  if __name__ == "__main__":
C:\Users\cs\anaconda3\envs\cuda_FYP1\lib\site-packages\ipykernel_launcher.py:15: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  from ipykernel import kernelapp as app
100%|██████████| 2197/2197 [08:12<00:00,  4.46it/s]


Dev


100%|██████████| 275/275 [00:13<00:00, 21.14it/s]


               precision    recall  f1-score   support

Not_offensive       0.83      0.50      0.62     25425
    not-Tamil       0.13      0.90      0.23      1454
    Offensive       0.41      0.49      0.45      8260

     accuracy                           0.51     35139
    macro avg       0.46      0.63      0.43     35139
 weighted avg       0.70      0.51      0.56     35139

               precision    recall  f1-score   support

Not_offensive       0.89      0.67      0.76      3193
    not-Tamil       0.33      0.90      0.49       172
    Offensive       0.46      0.68      0.54      1023

     accuracy                           0.68      4388
    macro avg       0.56      0.75      0.60      4388
 weighted avg       0.76      0.68      0.70      4388

Epoch 0, Train Loss = 0.70897757273988, Val Loss = 0.5320167241143915, Val F1 = 0.5977671953741631, Best Val f1 = 0.5977671953741631, stagnant = 0
Epoch 1
Train


...

               precision    recall  f1-score   support

Not_offensive       0.97      0.87      0.92     25425
    not-Tamil       0.74      0.99      0.85      1454
    Offensive       0.72      0.89      0.80      8260

     accuracy                           0.88     35139
    macro avg       0.81      0.92      0.85     35139
 weighted avg       0.90      0.88      0.88     35139

               precision    recall  f1-score   support

Not_offensive       0.90      0.83      0.86      3193
    not-Tamil       0.81      0.81      0.81       172
    Offensive       0.59      0.72      0.65      1023

     accuracy                           0.81      4388
    macro avg       0.76      0.79      0.77      4388
 weighted avg       0.82      0.81      0.81      4388

Epoch 21, Train Loss = 0.166300537224246, Val Loss = 0.9173777305593042, Val F1 = 0.7744171095886593, Best Val f1 = 0.7891972860928314, stagnant = 4
Epoch 22
Train


  0%|          | 0/2197 [00:00<?, ?it/s]C:\Users\cs\anaconda3\envs\cuda_FYP1\lib\site-packages\ipykernel_launcher.py:9: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  if __name__ == "__main__":
C:\Users\cs\anaconda3\envs\cuda_FYP1\lib\site-packages\ipykernel_launcher.py:15: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  from ipykernel import kernelapp as app
100%|██████████| 2197/2197 [08:12<00:00,  4.46it/s]


Dev


100%|██████████| 275/275 [00:13<00:00, 21.12it/s]

               precision    recall  f1-score   support

Not_offensive       0.97      0.88      0.92     25425
    not-Tamil       0.82      1.00      0.90      1454
    Offensive       0.73      0.91      0.81      8260

     accuracy                           0.89     35139
    macro avg       0.84      0.93      0.88     35139
 weighted avg       0.91      0.89      0.90     35139

               precision    recall  f1-score   support

Not_offensive       0.93      0.72      0.81      3193
    not-Tamil       0.77      0.84      0.81       172
    Offensive       0.50      0.84      0.63      1023

     accuracy                           0.75      4388
    macro avg       0.73      0.80      0.75      4388
 weighted avg       0.83      0.75      0.77      4388

Epoch 22, Train Loss = 0.14998409678154545, Val Loss = 0.9212417810765856, Val F1 = 0.747931392436132, Best Val f1 = 0.7891972860928314, stagnant = 5
No increase for 5 epochs, Stopping ...
